In [2]:
from e621_utilities import construct_text_description_from_json_entry
import json
from math import log
import random
import numpy as np
from collections import Counter


IMAGE_COUNT=None
INPUT_JSONS=['D:/PythonExperiments/e621_high_score.json','D:/PythonExperiments/e621_low_score.json']


def score_post_log_favs(post):
    return min(1.0, (log(int(post['fav_count'])+1) / 10))

def load_tag_sets(data_list):
    scores = []
    text_descriptions = []
    artists = []
    for data in data_list:
        text_description = construct_text_description_from_json_entry(data)
        artist, text_description = extract_artist(text_description)
        
        score =score_post_log_favs(data)
        score_int = round(score * 10)
        text_description.append(f"score:{score_int}")
        
        text_descriptions.append(text_description)
        artists.append(artist)
    return text_descriptions, artists

def load_data(input_json):
    with open(input_json) as f:
        data_list = json.load(f)[:IMAGE_COUNT] 
    # Load scores and tag sets from regular Python variables
    return load_tag_sets(data_list)

def extract_artist(tags):
    for tag in tags:
        if tag.startswith('by '):
            tags.remove(tag)
            return tag, tags
    return None, tags

#each of these variables is a list.  Each element of the list represents one instance
#in text_descriptions, a single element is a list of strings, where each string is a tag associated with the instance.
#in scores, a single element is the score associated with an instance
text_descriptions = []
artists = []
for input_json in INPUT_JSONS:
    sub_text_descriptions, sub_artists = load_data(input_json)
    text_descriptions.extend(sub_text_descriptions)
    artists.extend(sub_artists)


In [3]:
# Count the occurrences of each artist
artist_count = Counter(artists)

# Filter the data to keep only artists with 100 or more occurrences
min_occurrences = 100
filtered_text_descriptions = []
filtered_artists = []

for tags, artist in zip(text_descriptions, artists):
    if artist_count[artist] >= min_occurrences:
        filtered_text_descriptions.append(tags)
        filtered_artists.append(artist)

# Print the result
print(f"Artist Count Before Filtering: {len(set(artists))}")
print(f"Artist Count After Filtering: {len(set(filtered_artists))}")

Artist Count Before Filtering: 57134
Artist Count After Filtering: 698


In [4]:
from collections import defaultdict
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity


# Combine the tags of all images for each artist
artist_tags = defaultdict(list)
for tags, artist in zip(filtered_text_descriptions, filtered_artists):
    artist_tags[artist].extend(tags)

# Compute the TF-IDF representation for each artist
vectorizer = TfidfVectorizer(token_pattern=r'[^,]+')
X_artist = vectorizer.fit_transform([','.join(tags) for tags in artist_tags.values()])
artist_names = list(artist_tags.keys())

In [ ]:
# Given a new image with a tag list (excluding the artist name)
new_image_tags = []
new_tags_string = "airplane"
new_image_tags.extend(tag.strip() for tag in new_tags_string.split(","))

unseen_tags = set(new_image_tags) - set(vectorizer.vocabulary_.keys())
print(f'Unseen Tags:{unseen_tags}')

# Compute the TF-IDF representation for the new image
X_new_image = vectorizer.transform([','.join(new_image_tags)])

# Compute the cosine similarity between the new image and each artist
similarities = cosine_similarity(X_new_image, X_artist)[0]

# Rank the artists by their similarity scores and select the top 10
top_n = 20

# Top artists
top_artist_indices = np.argsort(similarities)[-top_n:][::-1]
top_artists = [(artist_names[i], similarities[i]) for i in top_artist_indices]

# Bottom artists
bottom_artist_indices = np.argsort(similarities)[:top_n]
bottom_artists = [(artist_names[i], similarities[i]) for i in bottom_artist_indices]

# Get the artist names from the top_artists and bottom_artists lists
top_artist_names = [artist for artist, _ in top_artists]
bottom_artist_names = [artist for artist, _ in bottom_artists]

# Print the top 10 artists with rank numbers and similarity scores
print("Top 10 artists:")
for rank, (artist, score) in enumerate(top_artists, start=1):
    print(f"{rank}. {artist} - similarity score: {score:.4f}")

# Print the top 10 artists as a comma-separated list
print("\nTop 10 artists:", ", ".join(str(artist) for artist in top_artist_names))

# Print the bottom 10 artists with rank numbers and similarity scores
print("\nBottom 10 artists:")
for rank, (artist, score) in enumerate(bottom_artists, start=1):
    print(f"{rank}. {artist} - similarity score: {score:.4f}")

# Print the bottom 10 artists as a comma-separated list
print("\nBottom 10 artists:", ", ".join(str(artist) for artist in bottom_artist_names))



In [6]:
import pandas as pd

def calculate_and_save_top_artists(tags, vectorizer, X_artist, artist_names, top_n):
    for tag in tags:
        new_image_tags = [tag.strip() for tag in tag.split(",")]

        # Compute the TF-IDF representation for the new image
        X_new_image = vectorizer.transform([','.join(new_image_tags)])

        # Compute the cosine similarity between the new image and each artist
        similarities = cosine_similarity(X_new_image, X_artist)[0]

        # Rank the artists by their similarity scores and select the top
        top_artist_indices = np.argsort(similarities)[-top_n:][::-1]
        top_artists = [(artist_names[i], similarities[i]) for i in top_artist_indices]

        # Create dataframes for artists and similarities
        artist_df = pd.DataFrame({tag: [artist for artist, _ in top_artists]}).T
        similarity_df = pd.DataFrame({tag: [f"{artist}({round(similarity, 3)})" for artist, similarity in top_artists]}).T

        # Append the data to csv files
        artist_df.to_csv('top_artists.csv', mode='a', header=False)
        similarity_df.to_csv('top_artists_similarity.csv', mode='a', header=False)

        
df = pd.read_csv('all_tags.csv')
unique_sorted_tags = df.iloc[:, 0].tolist()
# Use the function for all keys in the vocabulary
calculate_and_save_top_artists(unique_sorted_tags, vectorizer, X_artist, artist_names, 20)


In [3]:
import pandas as pd
import os

# Load the csv file
df = pd.read_csv('top_artists.csv')

# Directory to store the txt files
output_dir = 'e6ta'
os.makedirs(output_dir, exist_ok=True)  # Make sure the directory exists

# Characters that are not allowed in filenames
invalid_chars = ['/', '\\', ':', '*', '?', '"', '<', '>', '|']

# Loop through the DataFrame rows
for index, row in df.iterrows():
    # Get the name for the file (replace spaces with '_')
    filename = row[0].replace(' ', '_') + '.txt'
    
    # Check if the filename contains any invalid characters
    if any(char in filename for char in invalid_chars):
        print(f"Skipping tag '{row[0]}' due to invalid characters in the name.")
        continue

    # Get the first 10 tags, ignore any that are just whitespace
    tags = [str(tag).strip() for tag in row[1:11] if str(tag).strip()]

    # Create the txt file and write the tags
    with open(os.path.join(output_dir, filename), 'w') as f:
        f.write('\n'.join(tags))
        f.write('\n')  # Add a newline at the end of the file


Skipping tag ':3' due to invalid characters in the name.
Skipping tag ':<' due to invalid characters in the name.
Skipping tag ':d' due to invalid characters in the name.
Skipping tag ':o' due to invalid characters in the name.
Skipping tag '<3' due to invalid characters in the name.
Skipping tag '<3 censor' due to invalid characters in the name.
Skipping tag '<3 eyes' due to invalid characters in the name.
Skipping tag '<3 pupils' due to invalid characters in the name.
Skipping tag '?!' due to invalid characters in the name.
Skipping tag 'american dragon: jake long' due to invalid characters in the name.
Skipping tag 'dust: an elysian tail' due to invalid characters in the name.
Skipping tag 'five nights at freddy's: security breach' due to invalid characters in the name.
Skipping tag 'mao mao: heroes of pure heart' due to invalid characters in the name.
Skipping tag 'spirit: stallion of the cimarron' due to invalid characters in the name.
